In [1]:
import xarray as xr, numpy as np, pandas as pd
from sklearn.neighbors import KDTree
from skimage.transform import resize
import pathlib, yaml

In [2]:
with open('../input.yml') as f:
    input_data = yaml.load(f, Loader=yaml.loader.SafeLoader)

In [5]:
study_area = input_data['study_area']

year_range_train = range(input_data['training_period']['start'], input_data['training_period']['end']+1)
year_rainge_test = range(input_data['testing_period']['start'], input_data['testing_period']['end']+1)

data_in_dir = pathlib.Path(input_data['data_directories']['output']).joinpath(input_data['study_area'], 'input_data')
out_dir = pathlib.Path(input_data['data_directories']['output']).joinpath(input_data['study_area'], 'gp_sr')
out_dir.mkdir(parents=True, exist_ok=True)

In [6]:
extreme_days_in_dir = pathlib.Path(input_data['data_directories']['output']).joinpath(input_data['study_area'], 'extreme_days')

with open(extreme_days_in_dir/'extreme_days_era.npy', 'rb') as f:
    extreme_days_era = np.load(f)

In [11]:
with xr.open_dataset(data_in_dir/'era5_rainfall.nc') as ds:
    era_p = ds.rainfall

with xr.open_dataset(data_in_dir/'era5_land_rainfall.nc') as ds:
    era_land_p = ds.rainfall

In [43]:
era_p_train = era_p.where(era_p.time.isin(extreme_days_era[np.isin(pd.DatetimeIndex(extreme_days_era).year, year_range_train)]), drop=True)
era_land_p_train = era_land_p.where(era_land_p.time.isin(extreme_days_era[np.isin(pd.DatetimeIndex(extreme_days_era).year, year_range_train)]), drop=True)

In [44]:
xtrain = np.copy(era_p_train)
xtest = np.copy(era_p)
ytrain = np.copy(era_land_p_train)

In [45]:
xtrain_vec = np.reshape(xtrain, [np.shape(xtrain)[0], np.shape(xtrain)[1]*np.shape(xtrain)[2]])
ytrain_vec = np.reshape(ytrain, [np.shape(ytrain)[0], np.shape(ytrain)[1]*np.shape(ytrain)[2]])
xtest_vec = np.reshape(xtest, [np.shape(xtest)[0], np.shape(xtest)[1]*np.shape(xtest)[2]])

xtrain_vec_n = xtrain_vec - np.mean(xtrain_vec, 0)
ytrain_vec_n = ytrain_vec - np.mean(ytrain_vec, 0)

mdl = np.dot(np.dot(np.transpose(ytrain_vec_n), xtrain_vec_n), np.linalg.pinv(np.cov(np.transpose(xtrain_vec)))) / (np.shape(xtrain_vec)[0]-1)
tree = KDTree(xtrain_vec, metric='euclidean') # consider other distances
nnn = tree.query(xtest_vec, k=5, return_distance=False)

In [46]:
ymdl = np.empty([np.shape(xtest)[0], np.shape(ytrain)[1], np.shape(ytrain)[2]])

for i in range(np.shape(nnn)[0]):
    yreftot=np.empty([np.shape(nnn)[1], np.shape(ytrain_vec)[1]])
    xq = xtest_vec[i, :]

    for j in range(np.shape(nnn)[1]):
        xref = np.copy(xtrain_vec[nnn[i,j], :])
        yref = np.copy(ytrain_vec[nnn[i,j], :])

        for iter in range(0, 3):
            dy = np.dot(mdl, (xref-xq))
            yref = yref - dy
            xref = resize(np.reshape(yref, [np.shape(ytrain)[1], np.shape(ytrain)[2]]), [np.shape(xtrain)[1], np.shape(xtrain)[2]]).ravel()

        yreftot[j, :] = yref
    
    ymdl[i, :] = np.reshape(np.median(yreftot, 0), [np.shape(ytrain)[1], np.shape(ytrain)[2]])


In [50]:
ds = xr.Dataset(
    data_vars=dict(rainfall=(["time", "lon", "lat"], ymdl)),
    coords=dict(lon=era_land_p.lon.data, lat=era_land_p.lat.data, time=era_land_p.time),
    attrs=dict(description="ERA5 daily rainfall downscaled with Gaussian Process"),
)

ds.to_netcdf(out_dir/"era5_rainfall_sr.nc")